In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from itertools import islice
import datetime
from datetime import timedelta
import csv
from scipy.stats import norm
from scipy import stats
import git
import sys

In [2]:
repo = git.Repo("./", search_parent_directories=True)
homedir = repo.working_dir

In [3]:
def get_date(str1):
    counter = 0
    month = ""
    day = ""
    for x in str1:
        if counter == 1:
            month += x
        elif counter == 2:
            day += x
        if x == '-':
            counter += 1
    month = month[:-1]
    day = day[:-1]
    return (month, day)  

def get_fips(code):
    counter = 0
    fips = ""
    for x in code:
        if counter == 3:
            fips += x
        if x == '-':
            counter += 1
    return fips

In [4]:
# FIXES NANs

def fix_nans(submission, save=False):
	submission.fillna(method='ffill', inplace=True)
	# Do this stuff in the code that generates the error bounds instead of here
	num = submission._get_numeric_data()
	num[num < 0.1] = 0.00
	if save:
		submission.to_csv("modified_submission.csv", index=False)


In [5]:
def reformat(file1, file2, limit=10000.00, threshold=5000.0, ratio_max=5, normal_ratio=5, save=True):
    submission = pd.read_csv(file1, index_col=False)
    modified_submission = pd.read_csv(file2, index_col=False)
    fix_nans(submission)
    # convert to floats
    submission[["10", "20", "30", "40", "50", "60", "70", "80", "90"]] = submission[["10", "20", "30", "40", "50", "60", "70", "80", "90"]].apply(pd.to_numeric)
    
    final_submission = []
    
    forecast_dict = {}
    for index, row in submission.iterrows():
        current_id = row["id"]
        forecast = row.values
        
        fips = int(get_fips(current_id))
        date = get_date(current_id)
        
        #print(forecast[0])
        #print(forecast[1])
        # we don't care about performance after the next 2 weeks
        if int(date[0]) == 5 and int(date[1]) > 10:
                for i in range(1, 10):
                    if forecast[i] > limit and fips != 36061:
                        row[i] = limit

        elif int(date[0]) > 5:
            for i in range(1, 10):
                if forecast[i] > limit and fips != 36061:
                    row[i] = limit
        
        else:
            # if the 10th percentile is too big and not new york
            if forecast[1] > threshold and fips != 36061:
                # counties where deaths will be really small
                if fips == 21207 or fips == 1037 or fips == 48107 or fips == 47159:
                    # make it a normal distribution centered about 3 with std 0.5
                    mean, sigma = 3.0, 0.5
                    for i in range(1, 10):
                        j = min(i, 10 - i)
                        distribution = stats.norm.interval(1 - 0.2 * j, loc=mean, scale=sigma)
                        if i < 5:
                            row[i] = distribution[0]
                        elif i == 5:
                            row[i] = mean
                        else:
                            row[i] = distribution[1]
                # these counties will have more deaths, might be too big still
                else:
                    for i in range(1, 10):
                        row[i] /= 100
            
            # if the first prediction is 0 but the last is big
            #exists for 2 small counties w few deaths
            if forecast[1] == 0:
                if forecast[-1] > 1000:
                    mean, sigma = 2.0, 0.3
                    for i in range(1, 10):
                        j = min(i, 10 - i)
                        distribution = stats.norm.interval(1 - 0.2 * j, loc=mean, scale=sigma)
                        if i < 5:
                            row[i] = distribution[0]
                        elif i == 5:
                            row[i] = mean
                        else:
                            row[i] = distribution[1]
            
            else:
                # unreasonable 90th percentile to 10th percentile
                if forecast[-1] / forecast[1] > ratio_max:
                    # unreasonable 20th percentile to 10th percentile prediction, can't extrapolate from normal
                    if forecast[2] / forecast[1] > normal_ratio:
                        for i in range(1, 10):
                            row[i] = forecast[1] * (1 + float(i - 1)/10)
                    # we can extrapolate from normal distribution
                    else:
                        z1 = norm.ppf(forecast[1])
                        z2 = norm.ppf(forecast[2])
                        sigma = (forecast[2] - forecast[1]) / (z2 - z1)
                        mean = forecast[1] - sigma * z1
                        for i in range(1, 10):
                            j = min(i, 10 - i)
                            distribution = stats.norm.interval(1 - 0.2 * j, loc=mean, scale=sigma)
                            if i < 5:
                                row[i] = distribution[0]
                            elif i == 5:
                                row[i] = mean
                            else:
                                row[i] = distribution[1]
                                
        if forecast[-1] > 5000 and fips != 36061:
            if fips == 5061 or fips == 21207 or fips == 39075 or fips == 48365:
                mean, sigma = 3.0, 0.5
                for i in range(1, 10):
                    j = min(i, 10 - i)
                    distribution = stats.norm.interval(1 - 0.2 * j, loc=mean, scale=sigma)
                    if i < 5:
                        row[i] = distribution[0]
                    elif i == 5:
                        row[i] = mean
                    else:
                        row[i] = distribution[1]
                    
        forecast_dict[current_id] = row.values

    end = len(modified_submission)
    # for index, row in islice(modified_submission.iterrows(), start, end):
    for index, row in modified_submission.iterrows():
        print(f"{index} / {end}")
        current_id = row["id"]
        replacement = forecast_dict.pop(current_id, [current_id, 0.00, 0.00, 0.00, 0.00, 0.00, 0.00, 0.00, 0.00, 0.00]) 
        final_submission.append(replacement)

    if save:
        header = ["id", "10", "20", "30", "40", "50", "60", "70", "80", "90"]
        with open('formatted_submission.csv', 'w') as submission_file:
            writer = csv.writer(submission_file, delimiter=',')
            writer.writerow(header)
            writer.writerows(final_submission)

In [6]:
reformat("../predictions.csv", f"{homedir}/sample_submission.csv")

C:\Users\spar1\Anaconda3\lib\site-packages\scipy\stats\_distn_infrastructure.py:1996: RuntimeWarning: invalid value encountered in greater
  cond0 = self._argcheck(*args) & (scale > 0) & (loc == loc)


0 / 293293
1 / 293293
2 / 293293
3 / 293293
4 / 293293
5 / 293293
6 / 293293
7 / 293293
8 / 293293
9 / 293293
10 / 293293
11 / 293293
12 / 293293
13 / 293293
14 / 293293
15 / 293293
16 / 293293
17 / 293293
18 / 293293
19 / 293293
20 / 293293
21 / 293293
22 / 293293
23 / 293293
24 / 293293
25 / 293293
26 / 293293
27 / 293293
28 / 293293
29 / 293293
30 / 293293
31 / 293293
32 / 293293
33 / 293293
34 / 293293
35 / 293293
36 / 293293
37 / 293293
38 / 293293
39 / 293293
40 / 293293
41 / 293293
42 / 293293
43 / 293293
44 / 293293
45 / 293293
46 / 293293
47 / 293293
48 / 293293
49 / 293293
50 / 293293
51 / 293293
52 / 293293
53 / 293293
54 / 293293
55 / 293293
56 / 293293
57 / 293293
58 / 293293
59 / 293293
60 / 293293
61 / 293293
62 / 293293
63 / 293293
64 / 293293
65 / 293293
66 / 293293
67 / 293293
68 / 293293
69 / 293293
70 / 293293
71 / 293293
72 / 293293
73 / 293293
74 / 293293
75 / 293293
76 / 293293
77 / 293293
78 / 293293
79 / 293293
80 / 293293
81 / 293293
82 / 293293
83 / 293293
84

1079 / 293293
1080 / 293293
1081 / 293293
1082 / 293293
1083 / 293293
1084 / 293293
1085 / 293293
1086 / 293293
1087 / 293293
1088 / 293293
1089 / 293293
1090 / 293293
1091 / 293293
1092 / 293293
1093 / 293293
1094 / 293293
1095 / 293293
1096 / 293293
1097 / 293293
1098 / 293293
1099 / 293293
1100 / 293293
1101 / 293293
1102 / 293293
1103 / 293293
1104 / 293293
1105 / 293293
1106 / 293293
1107 / 293293
1108 / 293293
1109 / 293293
1110 / 293293
1111 / 293293
1112 / 293293
1113 / 293293
1114 / 293293
1115 / 293293
1116 / 293293
1117 / 293293
1118 / 293293
1119 / 293293
1120 / 293293
1121 / 293293
1122 / 293293
1123 / 293293
1124 / 293293
1125 / 293293
1126 / 293293
1127 / 293293
1128 / 293293
1129 / 293293
1130 / 293293
1131 / 293293
1132 / 293293
1133 / 293293
1134 / 293293
1135 / 293293
1136 / 293293
1137 / 293293
1138 / 293293
1139 / 293293
1140 / 293293
1141 / 293293
1142 / 293293
1143 / 293293
1144 / 293293
1145 / 293293
1146 / 293293
1147 / 293293
1148 / 293293
1149 / 293293
1150 /

2269 / 293293
2270 / 293293
2271 / 293293
2272 / 293293
2273 / 293293
2274 / 293293
2275 / 293293
2276 / 293293
2277 / 293293
2278 / 293293
2279 / 293293
2280 / 293293
2281 / 293293
2282 / 293293
2283 / 293293
2284 / 293293
2285 / 293293
2286 / 293293
2287 / 293293
2288 / 293293
2289 / 293293
2290 / 293293
2291 / 293293
2292 / 293293
2293 / 293293
2294 / 293293
2295 / 293293
2296 / 293293
2297 / 293293
2298 / 293293
2299 / 293293
2300 / 293293
2301 / 293293
2302 / 293293
2303 / 293293
2304 / 293293
2305 / 293293
2306 / 293293
2307 / 293293
2308 / 293293
2309 / 293293
2310 / 293293
2311 / 293293
2312 / 293293
2313 / 293293
2314 / 293293
2315 / 293293
2316 / 293293
2317 / 293293
2318 / 293293
2319 / 293293
2320 / 293293
2321 / 293293
2322 / 293293
2323 / 293293
2324 / 293293
2325 / 293293
2326 / 293293
2327 / 293293
2328 / 293293
2329 / 293293
2330 / 293293
2331 / 293293
2332 / 293293
2333 / 293293
2334 / 293293
2335 / 293293
2336 / 293293
2337 / 293293
2338 / 293293
2339 / 293293
2340 /

3410 / 293293
3411 / 293293
3412 / 293293
3413 / 293293
3414 / 293293
3415 / 293293
3416 / 293293
3417 / 293293
3418 / 293293
3419 / 293293
3420 / 293293
3421 / 293293
3422 / 293293
3423 / 293293
3424 / 293293
3425 / 293293
3426 / 293293
3427 / 293293
3428 / 293293
3429 / 293293
3430 / 293293
3431 / 293293
3432 / 293293
3433 / 293293
3434 / 293293
3435 / 293293
3436 / 293293
3437 / 293293
3438 / 293293
3439 / 293293
3440 / 293293
3441 / 293293
3442 / 293293
3443 / 293293
3444 / 293293
3445 / 293293
3446 / 293293
3447 / 293293
3448 / 293293
3449 / 293293
3450 / 293293
3451 / 293293
3452 / 293293
3453 / 293293
3454 / 293293
3455 / 293293
3456 / 293293
3457 / 293293
3458 / 293293
3459 / 293293
3460 / 293293
3461 / 293293
3462 / 293293
3463 / 293293
3464 / 293293
3465 / 293293
3466 / 293293
3467 / 293293
3468 / 293293
3469 / 293293
3470 / 293293
3471 / 293293
3472 / 293293
3473 / 293293
3474 / 293293
3475 / 293293
3476 / 293293
3477 / 293293
3478 / 293293
3479 / 293293
3480 / 293293
3481 /

...

287936 / 293293
287937 / 293293
287938 / 293293
287939 / 293293
287940 / 293293
287941 / 293293
287942 / 293293
287943 / 293293
287944 / 293293
287945 / 293293
287946 / 293293
287947 / 293293
287948 / 293293
287949 / 293293
287950 / 293293
287951 / 293293
287952 / 293293
287953 / 293293
287954 / 293293
287955 / 293293
287956 / 293293
287957 / 293293
287958 / 293293
287959 / 293293
287960 / 293293
287961 / 293293
287962 / 293293
287963 / 293293
287964 / 293293
287965 / 293293
287966 / 293293
287967 / 293293
287968 / 293293
287969 / 293293
287970 / 293293
287971 / 293293
287972 / 293293
287973 / 293293
287974 / 293293
287975 / 293293
287976 / 293293
287977 / 293293
287978 / 293293
287979 / 293293
287980 / 293293
287981 / 293293
287982 / 293293
287983 / 293293
287984 / 293293
287985 / 293293
287986 / 293293
287987 / 293293
287988 / 293293
287989 / 293293
287990 / 293293
287991 / 293293
287992 / 293293
287993 / 293293
287994 / 293293
287995 / 293293
287996 / 293293
287997 / 293293
287998 /

289118 / 293293
289119 / 293293
289120 / 293293
289121 / 293293
289122 / 293293
289123 / 293293
289124 / 293293
289125 / 293293
289126 / 293293
289127 / 293293
289128 / 293293
289129 / 293293
289130 / 293293
289131 / 293293
289132 / 293293
289133 / 293293
289134 / 293293
289135 / 293293
289136 / 293293
289137 / 293293
289138 / 293293
289139 / 293293
289140 / 293293
289141 / 293293
289142 / 293293
289143 / 293293
289144 / 293293
289145 / 293293
289146 / 293293
289147 / 293293
289148 / 293293
289149 / 293293
289150 / 293293
289151 / 293293
289152 / 293293
289153 / 293293
289154 / 293293
289155 / 293293
289156 / 293293
289157 / 293293
289158 / 293293
289159 / 293293
289160 / 293293
289161 / 293293
289162 / 293293
289163 / 293293
289164 / 293293
289165 / 293293
289166 / 293293
289167 / 293293
289168 / 293293
289169 / 293293
289170 / 293293
289171 / 293293
289172 / 293293
289173 / 293293
289174 / 293293
289175 / 293293
289176 / 293293
289177 / 293293
289178 / 293293
289179 / 293293
289180 /

290353 / 293293
290354 / 293293
290355 / 293293
290356 / 293293
290357 / 293293
290358 / 293293
290359 / 293293
290360 / 293293
290361 / 293293
290362 / 293293
290363 / 293293
290364 / 293293
290365 / 293293
290366 / 293293
290367 / 293293
290368 / 293293
290369 / 293293
290370 / 293293
290371 / 293293
290372 / 293293
290373 / 293293
290374 / 293293
290375 / 293293
290376 / 293293
290377 / 293293
290378 / 293293
290379 / 293293
290380 / 293293
290381 / 293293
290382 / 293293
290383 / 293293
290384 / 293293
290385 / 293293
290386 / 293293
290387 / 293293
290388 / 293293
290389 / 293293
290390 / 293293
290391 / 293293
290392 / 293293
290393 / 293293
290394 / 293293
290395 / 293293
290396 / 293293
290397 / 293293
290398 / 293293
290399 / 293293
290400 / 293293
290401 / 293293
290402 / 293293
290403 / 293293
290404 / 293293
290405 / 293293
290406 / 293293
290407 / 293293
290408 / 293293
290409 / 293293
290410 / 293293
290411 / 293293
290412 / 293293
290413 / 293293
290414 / 293293
290415 /

291483 / 293293
291484 / 293293
291485 / 293293
291486 / 293293
291487 / 293293
291488 / 293293
291489 / 293293
291490 / 293293
291491 / 293293
291492 / 293293
291493 / 293293
291494 / 293293
291495 / 293293
291496 / 293293
291497 / 293293
291498 / 293293
291499 / 293293
291500 / 293293
291501 / 293293
291502 / 293293
291503 / 293293
291504 / 293293
291505 / 293293
291506 / 293293
291507 / 293293
291508 / 293293
291509 / 293293
291510 / 293293
291511 / 293293
291512 / 293293
291513 / 293293
291514 / 293293
291515 / 293293
291516 / 293293
291517 / 293293
291518 / 293293
291519 / 293293
291520 / 293293
291521 / 293293
291522 / 293293
291523 / 293293
291524 / 293293
291525 / 293293
291526 / 293293
291527 / 293293
291528 / 293293
291529 / 293293
291530 / 293293
291531 / 293293
291532 / 293293
291533 / 293293
291534 / 293293
291535 / 293293
291536 / 293293
291537 / 293293
291538 / 293293
291539 / 293293
291540 / 293293
291541 / 293293
291542 / 293293
291543 / 293293
291544 / 293293
291545 /

292822 / 293293
292823 / 293293
292824 / 293293
292825 / 293293
292826 / 293293
292827 / 293293
292828 / 293293
292829 / 293293
292830 / 293293
292831 / 293293
292832 / 293293
292833 / 293293
292834 / 293293
292835 / 293293
292836 / 293293
292837 / 293293
292838 / 293293
292839 / 293293
292840 / 293293
292841 / 293293
292842 / 293293
292843 / 293293
292844 / 293293
292845 / 293293
292846 / 293293
292847 / 293293
292848 / 293293
292849 / 293293
292850 / 293293
292851 / 293293
292852 / 293293
292853 / 293293
292854 / 293293
292855 / 293293
292856 / 293293
292857 / 293293
292858 / 293293
292859 / 293293
292860 / 293293
292861 / 293293
292862 / 293293
292863 / 293293
292864 / 293293
292865 / 293293
292866 / 293293
292867 / 293293
292868 / 293293
292869 / 293293
292870 / 293293
292871 / 293293
292872 / 293293
292873 / 293293
292874 / 293293
292875 / 293293
292876 / 293293
292877 / 293293
292878 / 293293
292879 / 293293
292880 / 293293
292881 / 293293
292882 / 293293
292883 / 293293
292884 /